# # 모듈 및 함수
---

In [6]:
import numpy as np
import pandas as pd
import os
import glob
import torch
import re
import pickle as pkl
from sklearn.metrics import average_precision_score, precision_recall_curve
# from shapely.geometry.polygon import Polygon


def xywhn2xyxy(x, w=1920, h=1200):
    # Convert nx4 boxes from [x, y, w, h] to [x1, y1, x2, y2] where xy1=top-left, xy2=bottom-right
    x = np.array(x).reshape(1, -1)
    y = np.copy(x)
    y[:, 0] = (x[:, 0] - x[:, 2] / 2) * w  # top left x
    y[:, 1] = (x[:, 1] - x[:, 3] / 2) * h  # top left y
    y[:, 2] = (x[:, 0] + x[:, 2] / 2) * w  # bottom right x
    y[:, 3] = (x[:, 1] + x[:, 3] / 2) * h  # bottom right y
    y = list(np.around(y).astype(int).reshape(-1))
    return y
    
def cng2classname(classnum):
    cls_ls = {0: 'Small_Car',
              1: 'Light_Car',
              2: 'Car',
              3: 'Van',
              4: 'SUV',
              5: 'Small_Truck',
              6: 'Medium_Truck',
              7: 'Large_Truck',
              8: 'Mini_Bus',
              9: 'Large_Truck',
              10: 'Mini_Bus',
              11: 'Bus',
              12: 'Special_Vehicle',
              13: 'Two_Wheeler',
              14: 'Kickboard',
              15: 'Adult',
              16: 'Kid'}
    classname = cls_ls[classnum]
    return classname

In [ ]:
!pip install shapely

# # yolov5
---
- log 만들기

## # pred
---

In [ ]:
# yolov5 모델에서 예측값 뽑기

ck_path = "/data/NIA50/50-2/models/yolov5/runs/train/nia50_train1st3/weights/best.pt"
model = torch.hub.load('ultralytics/yolov5', 'custom', path=ck_path, device=2)
# model.cuda()
# device = torch.device(2)
# model.to(device)

with open('/data/NIA50/50-2/data/NIA50/train_1st/yolov5/ImageSets/val.txt', 'r') as f:
    vals = sorted([re.sub('\n', '', i) for i in f.readlines()])

deviding_num = 8
start_idx = 0

pred_df = pd.DataFrame()

for i in np.arange(deviding_num):
    end_idx = int(len(vals)/deviding_num * (i+1))
    detect_ls = vals[start_idx:end_idx]
    pred = model(detect_ls)
    
    scenes_len = len(detect_ls)
    for j, val in enumerate(detect_ls):
        scene_name = re.findall('[a-zA-Z0-9_]+', val)[-2]
        pred_temp = pred.pandas().xyxy[j]
        pred_temp['scene'] = [scene_name] * len(pred_temp)
        pred_df = pd.concat([pred_df, pred_temp])
    
    start_idx+=int(len(vals)/deviding_num)

pred_df.to_csv('/data/NIA50/50-2/data/NIA50/train_1st/yolov5/yolov5_log.csv')
pred_df

In [8]:
# 저장한 pred 불러오기

pred_df = pd.read_csv('/data/NIA50/50-2/data/NIA50/train_1st/yolov5/yolov5_log.csv', index_col = 0)

pred_df['x'] = (pred_df['xmin'] + pred_df['xmax'])/2
pred_df['y'] = (pred_df['ymin'] + pred_df['ymax'])/2
pred_df[['xmin', 'ymin', 'xmax', 'ymax', 'x', 'y']] = pred_df[['xmin', 'ymin', 'xmax', 'ymax', 'x', 'y']].apply(lambda row: row.astype(int))
pred_df['confidence'] = np.around(pred_df['confidence'], 2)
pred_df['pred'] = '-'
for i in np.arange(len(pred_df)):
    # pred_df['pred'].iloc[i] = list(pred_df[['scene', 'xmin', 'ymin', 'xmax', 'ymax', 'x', 'y', 'name', 'confidence']].iloc[i])
    pred_df['pred'].iloc[i] = list(pred_df[['xmin', 'ymin', 'xmax', 'ymax', 'x', 'y', 'name', 'confidence']].iloc[i])
pred_df

/tmp/ipykernel_32719/256757304.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  pred_df['pred'].iloc[i] = list(pred_df[['xmin', 'ymin', 'xmax', 'ymax', 'x', 'y', 'name', 'confidence']].iloc[i])
/tmp/ipykernel_32719/256757304.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  pred_df['pred'].iloc[i] = list(pred_df[['xmin', 'ymin', 'xmax', 'ymax', 'x', 'y', 'name', 'confidence']].iloc[i])
/tmp/ipykernel_32719/256757304.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexi

xmin  ymin  xmax  ymax  confidence  ...         name  \
0    164   747   489   954        0.96  ...          Car   
1    265   591   434   677        0.93  ...          Car   
2    543   642   732   765        0.92  ...          SUV   
3      4   753   281   960        0.92  ...          Car   
4    404   647   590   757        0.91  ...          Car   
..   ...   ...   ...   ...         ...  ...          ...   
15    89   374   320   454        0.45  ...    Small_Car   
16    91   375   323   452        0.39  ...          Car   
17  1649   836  1917  1006        0.37  ...  Two_Wheeler   
18  1312   323  1436   395        0.36  ...          Car   
19  1413   281  1524   367        0.29  ...          Car   

                           scene     x    y  \
0   Suwon_A_2210261635_0000_0001   326  851   
1   Suwon_A_2210261635_0000_0001   350  634   
2   Suwon_A_2210261635_0000_0001   637  704   
3   Suwon_A_2210261635_0000_0001   142  856   
4   Suwon_A_2210261635_0000_0001   497  702   
..                           ...   ...  ...   
15  Suwon_A_2211121422_0239_0002   204  414   
16  Suwon_A_2211121422_0239_0002   207  413   
17  Suwon_A_2211121422_0239_0002  1783  921   
18  Suwon_A_2211121422_0239_0002  1374  359   
19  Suwon_A_2211121422_0239_0002  1468  324   

                                                 pred  
0           [164, 747, 489, 954, 326, 851, Car, 0.96]  
1           [265, 591, 434, 677, 350, 634, Car, 0.93]  
2           [543, 642, 732, 765, 637, 704, SUV, 0.92]  
3             [4, 753, 281, 960, 142, 856, Car, 0.92]  
4           [404, 647, 590, 757, 497, 702, Car, 0.91]  
..                                                ...  
15     [89, 374, 320, 454, 204, 414, Small_Car, 0.45]  
16           [91, 375, 323, 452, 207, 413, Car, 0.39]  
17  [1649, 836, 1917, 1006, 1783, 921, Two_Wheeler...  
18       [1312, 323, 1436, 395, 1374, 359, Car, 0.36]  
19       [1413, 281, 1524, 367, 1468, 324, Car, 0.29]  

[7730 rows x 11 columns]

## # ground truth
---

In [9]:
def xywhn2xyxy(x, w=1920, h=1200):
    # Convert nx4 boxes from [x, y, w, h] to [x1, y1, x2, y2] where xy1=top-left, xy2=bottom-right
    x = np.array(x).reshape(1, -1)
    y = np.copy(x)
    y[:, 0] = (x[:, 0] - x[:, 2] / 2) * w  # top left x
    y[:, 1] = (x[:, 1] - x[:, 3] / 2) * h  # top left y
    y[:, 2] = (x[:, 0] + x[:, 2] / 2) * w  # bottom right x
    y[:, 3] = (x[:, 1] + x[:, 3] / 2) * h  # bottom right y
    y = list(np.around(y).astype(int).reshape(-1))
    return y
    
def cng2classname(classnum):
    cls_ls = {0: 'Small_Car',
              1: 'Light_Car',
              2: 'Car',
              3: 'Van',
              4: 'SUV',
              5: 'Small_Truck',
              6: 'Medium_Truck',
              7: 'Large_Truck',
              8: 'Mini_Bus',
              9: 'Large_Truck',
              10: 'Mini_Bus',
              11: 'Bus',
              12: 'Special_Vehicle',
              13: 'Two_Wheeler',
              14: 'Kickboard',
              15: 'Adult',
              16: 'Kid'}
    classname = cls_ls[classnum]
    return classname

In [10]:
with open('/data/NIA50/50-2/data/NIA50/train_1st/yolov5/ImageSets/val.txt', 'r') as f:
    vals = sorted([re.sub('\n', '', i) for i in f.readlines()])
scenes = [re.findall('[a-zA-Z0-9_]+', i)[-2] for i in vals]
# labels = sorted(glob.glob('/data/NIA50/50-2/data/NIA50/train_1st/yolov5/labels/*.txt'))
# val_labels = [i for i in labels if re.findall('[a-zA-Z0-9_]+', i)[-2] in i]

df = pd.DataFrame()
for scene in scenes:
    val_label = f'/data/NIA50/50-2/data/NIA50/train_1st/yolov5/labels/{scene}.txt'
    temp = pd.read_csv(val_label, sep='\s', names=['class_gt', 'x', 'y', 'w', 'h'], header=None, engine='python')
    temp['scene_gt'] = scene
    df = pd.concat([df, temp], axis = 0)

# df = pd.DataFrame()
# for scene, val_label in list(zip(scenes, val_labels)):
#     with open(val_label, 'r') as f:
#         val_label = f.readlines()

#     val_label = [re.sub('\n', '', i) for i in val_label]

#     temp = pd.read_csv(val_label, sep='\s', names=['class_gt', 'x', 'y', 'w', 'h'], header=None, engine='python')
#     temp['scene_gt'] = scene
#     df = pd.concat([df, temp], axis = 0)

df['xywhn'] = df[['x', 'y', 'w', 'h']].apply(lambda row: ' '.join(row.values.astype(str)), axis=1)
df['xyxy'] = df['xywhn'].apply(lambda x: xywhn2xyxy(list(map(float, x.split()))))
df['class_gt'] = df['class_gt'].apply(lambda x: cng2classname(x))
df['x'] = df['xyxy'].apply(lambda x: int((x[0] + x[2])/2))
df['y'] = df['xyxy'].apply(lambda x: int((x[1] + x[3])/2))
df['gt'] = '-'

for i in np.arange(len(df)):
    # df['gt'].iloc[i] = [df['scene_gt'].iloc[i]] + df['xyxy'].iloc[i] + [df['class_gt'].iloc[i]]
    df['gt'].iloc[i] = df['xyxy'].iloc[i] + list(df[['x', 'y']].iloc[i]) + [df['class_gt'].iloc[i]]

df

/tmp/ipykernel_32719/89812781.py:34: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['gt'].iloc[i] = df['xyxy'].iloc[i] + list(df[['x', 'y']].iloc[i]) + [df['class_gt'].iloc[i]]
/tmp/ipykernel_32719/89812781.py:34: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['gt'].iloc[i] = df['xyxy'].iloc[i] + list(df[['x', 'y']].iloc[i]) + [df['class_gt'].iloc[i]]
/tmp/ipykernel_32719/89812781.py:34: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


class_gt     x    y         w         h                      scene_gt  \
0     Adult  1359  615  0.029687  0.018333  Suwon_A_2210261635_0000_0001   
1     Adult  1265  597  0.022917  0.015000  Suwon_A_2210261635_0000_0001   
2     Adult  1319  579  0.023958  0.016667  Suwon_A_2210261635_0000_0001   
3     Adult  1161  579  0.013021  0.012500  Suwon_A_2210261635_0000_0001   
4     Adult  1153  597  0.014583  0.015000  Suwon_A_2210261635_0000_0001   
..      ...   ...  ...       ...       ...                           ...   
18      SUV   791  357  0.090104  0.071667  Suwon_A_2211121422_0239_0002   
19      SUV  1477  308  0.068750  0.082500  Suwon_A_2211121422_0239_0002   
20      SUV   417  291  0.073438  0.010833  Suwon_A_2211121422_0239_0002   
21      SUV   675  318  0.064583  0.030833  Suwon_A_2211121422_0239_0002   
22      Car   137  287  0.081771  0.026667  Suwon_A_2211121422_0239_0002   

                                                xywhn                    xyxy  \
0   0.7080729166666667 0.5125 0.0296875 0.01833333...  [1331, 604, 1388, 626]   
1   0.6588541666666666 0.4975 0.0229166666666666 0...  [1243, 588, 1287, 606]   
2   0.6869791666666667 0.4825 0.0239583333333333 0...  [1296, 569, 1342, 589]   
3   0.6049479166666667 0.4829166666666666 0.013020...  [1149, 572, 1174, 587]   
4   0.6005208333333333 0.4975 0.0145833333333333 0...  [1139, 588, 1167, 606]   
..                                                ...                     ...   
18  0.4122395833333333 0.2975 0.0901041666666666 0...    [705, 314, 878, 400]   
19  0.7692708333333333 0.2570833333333333 0.06875 ...  [1411, 259, 1543, 358]   
20  0.2174479166666666 0.2429166666666666 0.073437...    [347, 285, 488, 298]   
21  0.3515625 0.2654166666666667 0.064583333333333...    [613, 300, 737, 337]   
22  0.0716145833333333 0.2391666666666666 0.081770...     [59, 271, 216, 303]   

                                          gt  
0   [1331, 604, 1388, 626, 1359, 615, Adult]  
1   [1243, 588, 1287, 606, 1265, 597, Adult]  
2   [1296, 569, 1342, 589, 1319, 579, Adult]  
3   [1149, 572, 1174, 587, 1161, 579, Adult]  
4   [1139, 588, 1167, 606, 1153, 597, Adult]  
..                                       ...  
18       [705, 314, 878, 400, 791, 357, SUV]  
19    [1411, 259, 1543, 358, 1477, 308, SUV]  
20       [347, 285, 488, 298, 417, 291, SUV]  
21       [613, 300, 737, 337, 675, 318, SUV]  
22        [59, 271, 216, 303, 137, 287, Car]  

[8067 rows x 9 columns]

## # log 만들기
---

In [11]:
gt = df[['scene_gt', 'gt']]
pred = pred_df[['scene', 'pred']]

display(gt)
display(pred)

scene_gt                                        gt
0   Suwon_A_2210261635_0000_0001  [1331, 604, 1388, 626, 1359, 615, Adult]
1   Suwon_A_2210261635_0000_0001  [1243, 588, 1287, 606, 1265, 597, Adult]
2   Suwon_A_2210261635_0000_0001  [1296, 569, 1342, 589, 1319, 579, Adult]
3   Suwon_A_2210261635_0000_0001  [1149, 572, 1174, 587, 1161, 579, Adult]
4   Suwon_A_2210261635_0000_0001  [1139, 588, 1167, 606, 1153, 597, Adult]
..                           ...                                       ...
18  Suwon_A_2211121422_0239_0002       [705, 314, 878, 400, 791, 357, SUV]
19  Suwon_A_2211121422_0239_0002    [1411, 259, 1543, 358, 1477, 308, SUV]
20  Suwon_A_2211121422_0239_0002       [347, 285, 488, 298, 417, 291, SUV]
21  Suwon_A_2211121422_0239_0002       [613, 300, 737, 337, 675, 318, SUV]
22  Suwon_A_2211121422_0239_0002        [59, 271, 216, 303, 137, 287, Car]

[8067 rows x 2 columns]

scene  \
0   Suwon_A_2210261635_0000_0001   
1   Suwon_A_2210261635_0000_0001   
2   Suwon_A_2210261635_0000_0001   
3   Suwon_A_2210261635_0000_0001   
4   Suwon_A_2210261635_0000_0001   
..                           ...   
15  Suwon_A_2211121422_0239_0002   
16  Suwon_A_2211121422_0239_0002   
17  Suwon_A_2211121422_0239_0002   
18  Suwon_A_2211121422_0239_0002   
19  Suwon_A_2211121422_0239_0002   

                                                 pred  
0           [164, 747, 489, 954, 326, 851, Car, 0.96]  
1           [265, 591, 434, 677, 350, 634, Car, 0.93]  
2           [543, 642, 732, 765, 637, 704, SUV, 0.92]  
3             [4, 753, 281, 960, 142, 856, Car, 0.92]  
4           [404, 647, 590, 757, 497, 702, Car, 0.91]  
..                                                ...  
15     [89, 374, 320, 454, 204, 414, Small_Car, 0.45]  
16           [91, 375, 323, 452, 207, 413, Car, 0.39]  
17  [1649, 836, 1917, 1006, 1783, 921, Two_Wheeler...  
18       [1312, 323, 1436, 395, 1374, 359, Car, 0.36]  
19       [1413, 281, 1524, 367, 1468, 324, Car, 0.29]  

[7730 rows x 2 columns]

In [12]:
match_df = pd.DataFrame()
for scene in scenes:
    gt_tmp = gt.loc[gt['scene_gt']==scene]
    pred_tmp = pred.loc[pred['scene']==scene]

    gt_len = len(gt_tmp)
    pred_len = len(pred_tmp)

    tmp_df = pd.DataFrame(columns=['scene', 'gt', 'pred'])
    tmp_df['scene'] = [scene] * max(gt_len, pred_len)

    if gt_len >= pred_len:
        tmp_df['gt'] = gt_tmp['gt']
        tmp_df['pred'] = '-'
        for i, gt_label in enumerate(gt_tmp['gt']):
            for pred_label in pred_tmp['pred']:
                if (gt_label[4] - 20) < pred_label[4] < (gt_label[4] + 20) and (gt_label[5] - 20) < pred_label[5] < (gt_label[5] + 20):
                    tmp_df['pred'].iloc[i] = pred_label

    elif gt_len < pred_len:
        tmp_df['pred'] = pred_tmp['pred']
        tmp_df['gt'] = '-'
        for i, pred_label in enumerate(pred_tmp['pred']):
            for gt_label in gt_tmp['gt']:
                if (gt_label[4] - 20) < pred_label[4] < (gt_label[4] + 20) and (gt_label[5] - 20) < pred_label[5] < (gt_label[5] + 20):
                    tmp_df['gt'].iloc[i] = gt_label
    
    match_df = pd.concat([match_df, tmp_df])
    match_df.reset_index(drop=True, inplace=True)

match_df

scene                                        gt  \
0     Suwon_A_2210261635_0000_0001  [1331, 604, 1388, 626, 1359, 615, Adult]   
1     Suwon_A_2210261635_0000_0001  [1243, 588, 1287, 606, 1265, 597, Adult]   
2     Suwon_A_2210261635_0000_0001  [1296, 569, 1342, 589, 1319, 579, Adult]   
3     Suwon_A_2210261635_0000_0001  [1149, 572, 1174, 587, 1161, 579, Adult]   
4     Suwon_A_2210261635_0000_0001  [1139, 588, 1167, 606, 1153, 597, Adult]   
...                            ...                                       ...   
8446  Suwon_A_2211121422_0239_0002       [705, 314, 878, 400, 791, 357, SUV]   
8447  Suwon_A_2211121422_0239_0002    [1411, 259, 1543, 358, 1477, 308, SUV]   
8448  Suwon_A_2211121422_0239_0002       [347, 285, 488, 298, 417, 291, SUV]   
8449  Suwon_A_2211121422_0239_0002       [613, 300, 737, 337, 675, 318, SUV]   
8450  Suwon_A_2211121422_0239_0002        [59, 271, 216, 303, 137, 287, Car]   

                                                pred  
0     [1336, 596, 1387, 623, 1362, 609, Adult, 0.78]  
1     [1238, 586, 1288, 608, 1263, 597, Adult, 0.78]  
2     [1295, 566, 1340, 589, 1317, 577, Adult, 0.63]  
3     [1134, 582, 1177, 604, 1156, 593, Adult, 0.66]  
4     [1134, 582, 1177, 604, 1156, 593, Adult, 0.66]  
...                                              ...  
8446       [704, 315, 895, 404, 799, 360, SUV, 0.77]  
8447    [1413, 281, 1524, 367, 1468, 324, Car, 0.29]  
8448                                               -  
8449                                               -  
8450                                               -  

[8451 rows x 3 columns]

In [89]:
match_df2 = match_df.copy()
# match_df2.reset_index(drop=True, inplace=True)
match_df2['confidence'] = '-'
match_df2['IoU'] = '-'
match_df2['confusion_matrix'] = '-'
match_df2['sum_tp'] = '-'
match_df2['sum_fp'] = '-'
match_df2['precision'] = '-'
match_df2['recall'] = '-'

match_df2.loc[match_df2['gt']!='-', 'gt'] = match_df.loc[match_df['gt']!='-', 'gt'].apply(lambda x: x[0:4] + [x[6]])
match_df2.loc[match_df2['gt']!='-', 'gt_class'] = match_df.loc[match_df['gt']!='-', 'gt'].apply(lambda x: x[6])
match_df2.loc[match_df2['pred']!='-', 'pred'] = match_df.loc[match_df['pred']!='-', 'pred'].apply(lambda x: x[0:4] + [x[6]])
match_df2.loc[match_df2['pred']!='-', 'pred_class'] = match_df.loc[match_df['pred']!='-', 'pred'].apply(lambda x: x[6])
match_df2.loc[match_df2['pred']!='-', 'confidence'] = match_df.loc[match_df['pred']!='-', 'pred'].apply(lambda x: x[7])
# match_df2['gt'] = match_df['gt'].apply(lambda x: x[:4] + [x[6]])

# IoU 계산하기
both_gt_pred = match_df2.loc[(match_df2['gt']!='-') & (match_df2['pred']!='-')]
for i in both_gt_pred.index:
    # gt = match_df2.loc[(match_df2['gt']!='-') & (match_df2['pred']!='-'), 'gt'].iloc[i]
    # pred = match_df2.loc[(match_df2['gt']!='-') & (match_df2['pred']!='-'), 'pred'].iloc[i]
    gt = both_gt_pred['gt'].loc[i]
    pred = both_gt_pred['pred'].loc[i]

    intersection_x_len = min(gt[2], pred[2]) - max(gt[0], pred[0])
    intersection_y_len = min(gt[3], pred[3]) - max(gt[1], pred[1])
    intersection_area = intersection_x_len * intersection_y_len

    gt_area = (gt[2] - gt[0]) * (gt[3] - gt[1])
    pred_area = (pred[2] - pred[0]) * (pred[3] - pred[1])

    iou = intersection_area / (gt_area + pred_area - intersection_area)

    match_df2['IoU'].loc[i] = np.around(iou, 2)

both_gt_pred = match_df2.loc[(match_df2['gt']!='-') & (match_df2['pred']!='-')]
for i in both_gt_pred.index:
    if both_gt_pred['gt'].loc[i][4] == both_gt_pred['pred'].loc[i][4] and both_gt_pred['IoU'].loc[i] >= 0.5:
        match_df2['confusion_matrix'].loc[i] = 'TP'

match_df2.loc[match_df2['confusion_matrix']!='TP', 'confusion_matrix'] = 'FP'

# for class_ in match_df2['gt_class'].unique():
#     tp = match_df2.loc[(match_df2['gt_class']==class_) & (match_df2['pred_class']==class_) & (match_df2['confusion_matrix']=='TP')]
#     fp = match_df2.loc[(match_df2['gt_class']==class_) & (match_df2['pred_class']==class_) & (match_df2['confusion_matrix']=='FP')]

#     sum_tp = np.arange(len(tp)) + 1
#     sum_fp = np.arange(len(fp)) + 1
    
#     match_df2.loc[(match_df2['gt_class']==class_) & (match_df2['pred_class']==class_) & (match_df2['confusion_matrix']=='TP'), 'sum_tp'] = sum_tp
#     match_df2.loc[(match_df2['gt_class']==class_) & (match_df2['pred_class']==class_) & (match_df2['confusion_matrix']=='FP'), 'sum_fp'] = sum_fp


match_df2.replace('-', np.NaN, inplace=True)

for class_ in match_df2['gt_class'].unique():
    tp = match_df2.loc[(match_df2['gt_class']==class_) & (match_df2['confusion_matrix']=='TP')]
    fp = match_df2.loc[((match_df2['gt_class']==class_) & (match_df2['confusion_matrix']=='FP')) | ((match_df2['gt_class'].isnull()) & (match_df2['pred_class']==class_))]
    # fp = match_df2.loc[((match_df2['gt_class']==class_) \
    #     | ((match_df2['gt_class']==np.NaN) & (match_df2['pred_class']==class_))) & \
    #         (match_df2['confusion_matrix']=='FP')]

    sum_tp = np.arange(len(tp)) + 1
    sum_fp = np.arange(len(fp)) + 1
    
    match_df2.loc[(match_df2['gt_class']==class_) & (match_df2['confusion_matrix']=='TP'), 'sum_tp'] = sum_tp
    match_df2.loc[((match_df2['gt_class']==class_) & (match_df2['confusion_matrix']=='FP')) | ((match_df2['gt_class'].isnull()) & (match_df2['pred_class']==class_)), 'sum_fp'] = sum_fp
    # match_df2.loc[((match_df2['gt_class']==class_) \
    #     | ((match_df2['gt_class']==np.NaN) & (match_df2['pred_class']==class_))) & \
    #         (match_df2['confusion_matrix']=='FP'), 'sum_fp'] = sum_fp

    match_df2.loc[(match_df2['gt_class']==class_), 'sum_tp'] = match_df2.loc[(match_df2['gt_class']==class_), 'sum_tp'].fillna(method='ffill')
    match_df2.loc[(match_df2['gt_class']==class_), 'sum_fp'] = match_df2.loc[(match_df2['gt_class']==class_), 'sum_fp'].fillna(method='ffill')
    match_df2.loc[(match_df2['gt_class']==class_), ['sum_tp', 'sum_fp']] = match_df2.loc[(match_df2['gt_class']==class_), ['sum_tp', 'sum_fp']].fillna(0)
    
    class_df = match_df2.loc[(match_df2['gt_class']==class_)]
    match_df2.loc[(match_df2['gt_class']==class_), 'precision'] = np.around(class_df['sum_tp']/(class_df['sum_tp']+class_df['sum_fp']), 3)
    match_df2.loc[(match_df2['gt_class']==class_), 'recall'] = np.around(class_df['sum_tp']/len(class_df), 3)
# match_df2['sum_tp'].fillna(method='ffill', inplace=True)
# match_df2['sum_fp'].fillna(method='ffill', inplace=True)
# match_df2['sum_tp'].fillna(0, inplace=True)
# match_df2['sum_fp'].fillna(0, inplace=True)
# match_df2.loc[match_df2['confusion_matrix']=='TP', 'confusion_matrix_fig'] = 1
# match_df2.loc[match_df2['confusion_matrix']=='FP', 'confusion_matrix_fig'] = 0
# match_df2['confusion_matrix_fig'] = match_df2['confusion_matrix_fig'].astype(int)
match_df2.fillna('-', inplace=True)
match_df2

scene                             gt  \
0     Suwon_A_2210261635_0000_0001  [1331, 604, 1388, 626, Adult]   
1     Suwon_A_2210261635_0000_0001  [1243, 588, 1287, 606, Adult]   
2     Suwon_A_2210261635_0000_0001  [1296, 569, 1342, 589, Adult]   
3     Suwon_A_2210261635_0000_0001  [1149, 572, 1174, 587, Adult]   
4     Suwon_A_2210261635_0000_0001  [1139, 588, 1167, 606, Adult]   
...                            ...                            ...   
8446  Suwon_A_2211121422_0239_0002      [705, 314, 878, 400, SUV]   
8447  Suwon_A_2211121422_0239_0002    [1411, 259, 1543, 358, SUV]   
8448  Suwon_A_2211121422_0239_0002      [347, 285, 488, 298, SUV]   
8449  Suwon_A_2211121422_0239_0002      [613, 300, 737, 337, SUV]   
8450  Suwon_A_2211121422_0239_0002       [59, 271, 216, 303, Car]   

                               pred confidence   IoU  ... sum_fp precision  \
0     [1336, 596, 1387, 623, Adult]       0.78  0.58  ...    0.0       1.0   
1     [1238, 586, 1288, 608, Adult]       0.78  0.72  ...    0.0       1.0   
2     [1295, 566, 1340, 589, Adult]       0.63  0.82  ...    0.0       1.0   
3     [1134, 582, 1177, 604, Adult]       0.66   0.1  ...    1.0      0.75   
4     [1134, 582, 1177, 604, Adult]       0.66  0.45  ...    2.0       0.6   
...                             ...        ...   ...  ...    ...       ...   
8446      [704, 315, 895, 404, SUV]       0.77  0.86  ...  449.0     0.744   
8447    [1413, 281, 1524, 367, Car]       0.29  0.61  ...  450.0     0.743   
8448                              -          -     -  ...  451.0     0.743   
8449                              -          -     -  ...  452.0     0.742   
8450                              -          -     -  ...  832.0     0.744   

      recall gt_class pred_class  
0      0.001    Adult      Adult  
1      0.001    Adult      Adult  
2      0.002    Adult      Adult  
3      0.002    Adult      Adult  
4      0.002    Adult      Adult  
...      ...      ...        ...  
8446   0.766      SUV        SUV  
8447   0.766      SUV        Car  
8448   0.766      SUV          -  
8449   0.766      SUV          -  
8450   0.777      Car          -  

[8451 rows x 12 columns]

In [90]:
# 결과값 저장

match_df2.iloc[:, :-2].to_csv('/data/NIA50/50-2/data/NIA50/train_1st/yolov5/yolov5_mAP_log.csv', index = False)